In [2]:
%matplotlib inline

import os
import pandas as pd
import dlisio
import lasio as ls
#import selenium
#import phantomjs
import matplotlib.pyplot as plt
import numpy as np
import numpy.lib.recfunctions as rfn
#import re
#from azure.datalake.store import core, lib
#import tempfile
import sys
import hvplot.pandas
import holoviews as hv
from holoviews import opts, streams
from holoviews.plotting.links import DataLink
hv.extension('bokeh', logo=None)
from IPython.display import display, HTML
from bokeh.models.tools import LassoSelectTool, BoxSelectTool  # tools=['hover']
box_select = BoxSelectTool()
lasso_select = LassoSelectTool()
import panel as pn
pn.extension()
from IPython.display import display, HTML

client_secret = "Bw2w*31.CmbIiP.i2EILQ=HN@xr]yeu?"

display(HTML(data="""
<style>
    div#notebook-container    { width: 95%; }
    div#menubar-container     { width: 65%; }
    div#maintoolbar-container { width: 60%; }
</style>
"""))

## Make LAS from scratch

In [68]:
from datetime import datetime

In [69]:
def las_from_scratch(wellname, filename, start=1000, stop=3000, step=0.5):
    lasfile = ls.LASFile()
    lasfile.well.DATE = datetime.today().strftime('%Y-%m-%d %H:%M:%S')
    lasfile.well.WELL.value = wellname
    lasfile.params['TEST'] = ls.HeaderItem('TEST', value='First Test')
    lasfile.other = 'LAS-file created from scratch'
    depths = np.arange(start, stop, step)
    lasfile.add_curve('DEPTH (m)', depths, unit='m')
    return lasfile, depths

In [70]:
def add_fakedata(fakenames, fake_eq, lfs_sample): # (Name of fake curve (parameter), equation to produce fake data, las_from_scratch_sample)
    fake = fake_eq
    #fake[:3] = np.nan # Set first ten values to NaN
    lfs_sample.add_curve(fakenames[0], fake, descr=fakenames[1]) # (parameter-name, values, description)
    return

In [71]:
fakewell1, depths = las_from_scratch('FAKEWELL_1', 'fakewell1.las')

## Set parameters and equation

In [72]:
params = [['GR', 'Gamma Ray'], ['RD', 'Deep Resistivity'], ['RM', 'Medium Resistivity'], ['RS', 'Shallow Resistivity'], 
         ['NPHI', 'Neutron Porosity'], ['RHOB', 'Density'], ['DT', 'Sonic Velocity'], ['CALI', 'Caliper'], ['BS', 'Bit Size']]

equations = [np.log10(depths)*5 + np.sin(len(depths)) + np.random.random(len(depths)), np.log(depths)/np.exp(depths/1000) + np.random.random(len(depths)),
            np.cos(depths)*np.sin(depths), np.tan(depths)*len(depths)/10, np.exp(depths/1000),
            np.sin(depths)+np.random.random(len(depths)), 10 - np.random.random(len(depths))*np.sin(depths),
            5 - np.log(depths/10) + 5*np.sin(len(depths)), depths*np.log(len(depths)/10)]

In [73]:
def add_multiple_fakedata(lfs_sample, equations, param_list):
    [add_fakedata([param_list[i][0], param_list[i][1]], equations[i], lfs_sample) for i in range(len(param_list))]

In [74]:
add_multiple_fakedata(fakewell1, equations, params)

In [75]:
fakewell1.write('fakewell1.las', version=2)

## Make dataframe from LAS

In [49]:
def las_to_df(lasfile):
    df = lasfile.df()
    df.reset_index(inplace=True)
    df['WELLNAME'] = lasfile.well.WELL.value
    return df

In [66]:
fakewell1_df = las_to_df(fakewell1)

In [59]:
def get_numerics(df, depthcurvename):
    curve_list=list(df.columns[(df.dtypes.values == np.dtype('float64'))])
    curve_list.remove(depthcurvename)
    return curve_list;

curve_list = get_numerics(fakewell1_df, 'DEPTH (m)')
curve_list

['GR', 'RD', 'RM', 'RS', 'NPHI', 'RHOB', 'DT', 'CALI', 'BS']

In [58]:
def curve_plot_numerics(log, df, depthname, group='WELLNAME', alpha=1):
  aplot = df.hvplot(x=depthname, y=log, by=group ,invert=True, flip_yaxis=True, shared_axes=True, alpha=alpha,
                       height=600, width=300).opts(fontsize={'labels': 16,'xticks': 14, 'yticks': 14})
  return aplot;

In [67]:
plotlist = [curve_plot_numerics(x, df=fakewell1_df, depthname='DEPTH (m)') for x in curve_list]
plotz = hv.Layout(plotlist).cols(len(curve_list))
plotz

:Layout
   .NdOverlay.I    :NdOverlay   [WELLNAME]
      :Curve   [DEPTH (m)]   (GR)
   .NdOverlay.II   :NdOverlay   [WELLNAME]
      :Curve   [DEPTH (m)]   (RD)
   .NdOverlay.III  :NdOverlay   [WELLNAME]
      :Curve   [DEPTH (m)]   (RM)
   .NdOverlay.IV   :NdOverlay   [WELLNAME]
      :Curve   [DEPTH (m)]   (RS)
   .NdOverlay.V    :NdOverlay   [WELLNAME]
      :Curve   [DEPTH (m)]   (NPHI)
   .NdOverlay.VI   :NdOverlay   [WELLNAME]
      :Curve   [DEPTH (m)]   (RHOB)
   .NdOverlay.VII  :NdOverlay   [WELLNAME]
      :Curve   [DEPTH (m)]   (DT)
   .NdOverlay.VIII :NdOverlay   [WELLNAME]
      :Curve   [DEPTH (m)]   (CALI)
   .NdOverlay.IX   :NdOverlay   [WELLNAME]
      :Curve   [DEPTH (m)]   (BS)